In [44]:
import pandas as pd
import matplotlib.pyplot as plt
%matplotlib inline
import seaborn as sns
import numpy as np
from tqdm import tqdm 
sns.set_style("darkgrid")
from datetime import datetime
import json
import matplotlib as mpl
import time



# Text mining
import re
import nltk
from nltk import word_tokenize
from nltk.stem import WordNetLemmatizer 
lemmatizer = WordNetLemmatizer()
nltk.download("stopwords")
nltk.download('punkt')
nltk.download('wordnet')
from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer

# Folium maps
import folium
from folium.plugins import MarkerCluster
from folium.plugins import FastMarkerCluster

# For places
from helperfunctions import get_country_specific_information, get_coordinates, get_geojson_grid, draw_grid, generateBaseMap
NY_location, L_location, NY_num, L_num = get_country_specific_information()

[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/akterminsprove/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     /Users/akterminsprove/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     /Users/akterminsprove/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [45]:
data_path = "data/"
places = pd.read_csv(data_path + "places.csv", sep=";")
reviews = pd.read_csv(data_path + "reviews.csv", sep=";", low_memory=False)

In [46]:
places.shape

(102851, 8)

# Data preprocessing

First, the data for the places is cleaned by first looking into the places features, and then by placing a grid on top of the two cities to ensure, that we only include places that are within the city center and to define the zones used for the modeling.

Secondly, the review texts are cleaned from stopwords and lemmatized and the categories for each business are cleaned to only include the top 1 most common categori for each business. 

## 1.1 Places

In [47]:
# Quick overwiew of the attributes in the places data file
# 102851 places with 7 features
places.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 102851 entries, 0 to 102850
Data columns (total 8 columns):
 #   Column        Non-Null Count   Dtype 
---  ------        --------------   ----- 
 0   name          102851 non-null  object
 1   price         30486 non-null   object
 2   address       102851 non-null  object
 3   hours         65403 non-null   object
 4   phone         98390 non-null   object
 5   closed        102851 non-null  bool  
 6   gPlusPlaceId  102851 non-null  object
 7   gps           101600 non-null  object
dtypes: bool(1), object(7)
memory usage: 5.6+ MB


In [48]:
# Lets consider the missing values
# Only interested in restoring / removing missing values for Price and GPS
places.isna().sum()

name                0
price           72365
address             0
hours           37448
phone            4461
closed              0
gPlusPlaceId        0
gps              1251
dtype: int64

In [49]:
# First, we have to remove places that are currently closed
places = places.loc[places.closed == False ].reset_index(drop=True)

# That leaves ud with 96497 places across NY state and London
places.shape

(96497, 8)

In [50]:
# Remove places that does not have coordinates
places = places.loc[places.gps.isna()==False].reset_index(drop=True)

# Then we clean the GPS coordinates to become latitiude and longitude
places['lat'] = [float(i.strip('][').split(', ')[0]) for i in places.gps]
places['lon'] = [float(i.strip('][').split(', ')[1]) for i in places.gps]

In [51]:
# We have some missing values in the price, we wish to predict these based on other features

# But first, we convert price ranges into three categories
# $ = £
# $$ = ££
# $$$ = £££
# For some reason, it seems that businesses with more currency signs are actually cheaper

places['price_cat'] = np.nan
helper = 2
for i in range(1,4):
    indexes = places.loc[(places.price == "$"*i) |(places.price == "£"*i)].index
    places.loc[indexes, 'price_cat'] = i+helper
    helper -= 2

places['price_cat'] = places.price_cat.astype('category')

# Now the values have been filled in
places.price_cat.value_counts()


2.0    15484
1.0     9124
3.0     3151
Name: price_cat, dtype: int64

In [52]:
# Make a feature that can distinguish between places in United Kingdom (London), NY city and outside of these cities

places['city'] = np.nan

for num,adress in tqdm(enumerate(places.address)):

    # Clean adress
    i = adress.strip('][').split(',')[-1]
    # Check if in NY
    in_ny = re.findall(r"NY\s100\d{2}", i)
    # Check if in United Kingdom aka London
    in_london = re.findall(r'United Kingdom', i)

    if len(in_ny)>0:

        places.loc[num, 'city'] = 'New York'

    elif len(in_london)>0:

        places.loc[num, 'city'] = 'London' 

    else:
        places.loc[num, 'city'] = 'Remove' 

    

95443it [02:19, 681.94it/s]


In [53]:
# See the number of places in United Kingdom and New York 
places.city.value_counts()

Remove      52027
London      26451
New York    16965
Name: city, dtype: int64

In [54]:
# Remove places that are not in United Kingdom or New York
places = places.loc[places.city.isin(['New York','London'])]

In [55]:
# Drop features, that we are not going to use: Adress, Hours, Phone, GPS
# Rename price_cat to price
places = places[['gPlusPlaceId','name','price_cat','lat','lon','city', 'address']].rename(columns={'price_cat':"price"}).reset_index(drop=True)
places.head(4)

gPlusPlaceId                                         name price  \
0  102297455696045037925                           HSBC Head Quarters   NaN   
1  107630647505995708542  Consulate General of the Republic of Poland   NaN   
2  104388257267586837092                          Blockbuster Express   1.0   
3  101742583391038750118                                 Carpo London   NaN   

         lat        lon      city  \
0  51.506582  -0.016885    London   
1  40.749680 -73.981173  New York   
2  40.815224 -73.958116  New York   
3  51.509499  -0.135762    London   

                                             address  
0  ['8 Canada Sq', 'London E14 5HQ', 'United King...  
1          ['233 Madison Ave', 'New York, NY 10016']  
2       ['568-574 W 125th St', 'New York, NY 10027']  
3  ['16 Piccadilly', 'London W1J 0DE', 'United Ki...

In [56]:
# Adress are stored as a "['Adress']", thus we use regex to find the word between the apostrophes
places['address'] = places.address.apply(lambda x: re.findall(r"[\[|\s]\'(.*?)\'[\,|\]]", x))
places['address'] = places['address'].apply(lambda x: ", ".join(x))

### Visualization of places in United Kingdom (London) and New York

In [57]:
def CreateScatterMap(df_folium_map, coordinates):

    scatter_map = generateBaseMap(default_location = coordinates)
    mc = MarkerCluster()

    for index,row in df_folium_map.iterrows():  
        latlon = row[["lat","lon"]]
        labels = row['address'].strip('][').replace("'","")

        mc.add_child(FastMarkerCluster([latlon.iloc[0], latlon.iloc[1]], popup = labels))
        mc.add_child(folium.Marker(location=[latlon.iloc[0], latlon.iloc[1]], popup = labels))

    scatter_map.add_child(mc)

    return scatter_map

In [58]:
def CreateFastScatterMap(df_folium_map, coordinates):

    scatter_map = generateBaseMap(default_location = coordinates)
    scatter_map.add_child(FastMarkerCluster(df_folium_map[['lat','lon']].values.tolist()))

    return scatter_map

In [59]:
# Visualize places in New York
df_folium_map_NY=places.loc[places.city == 'New York'][['gPlusPlaceId','lat','lon', 'address']].set_index('gPlusPlaceId')
scatter_map = CreateFastScatterMap(df_folium_map_NY,NY_location)
scatter_map

In [60]:
# Visualize places in London
df_folium_map_L = places.loc[places.city == 'London'][['gPlusPlaceId','lat','lon', 'address']].set_index('gPlusPlaceId')#.head(5000)

scatter_map = CreateFastScatterMap(df_folium_map_L, L_location)
scatter_map

### Place a grid on top of New York and London
Take a look at some of the defined helper functions, in the **helperfunctions.py** file to understand how the grids are plotted using folium.

In [61]:
def create_grid(df, city, num):
    df['Grid'] = np.nan
    
    bottomLeft, bottomRight, topLeft, topRight = get_coordinates(city)

    cols = np.linspace(bottomLeft[1], bottomRight[1], num=num)
    rows = np.linspace(bottomLeft[0], topLeft[0], num=num)


    num = 0
    for i in range(len(rows)-1):
        for j in range(len(cols)-1):
            for index,row in df.loc[(df.lon >= cols[j]) & (df.lon <= cols[j+1]) & (df.lat >= rows[i]) & (df.lat <= rows[i+1])].iterrows():
                    df.loc[index, "Grid"] = num 

            
            num += 1

    return df

In [62]:
# Create a grid for New York
df_test = places.loc[places.city =='New York'].reset_index(drop=True)
df_NY = create_grid(df_test, "New York", NY_num)
grid = get_geojson_grid("New York", n=NY_num-1)
draw_grid(grid, NY_location)

In [63]:
# Create a grid for London
df_test = places.loc[places.city =='London'].reset_index(drop=True)
df_L = create_grid(df_test, "London", L_num)
grid = get_geojson_grid("London", n=L_num-1)
draw_grid(grid, L_location)

In [64]:
# Calculate size of grid cells
from math import sin, cos, sqrt, atan2, radians

def distance(lat1,lon1,lat2,lon2):

    # approximate radius of earth in km
    R = 6373.0

    dlon = lon2 - lon1
    dlat = lat2 - lat1

    a = sin(dlat / 2)**2 + cos(lat1) * cos(lat2) * sin(dlon / 2)**2
    c = 2 * atan2(sqrt(a), sqrt(1 - a))

    distance = R * c

    
    return distance


def GridSize(city, num):

    bottomLeft, bottomRight, topLeft, topRight = get_coordinates(city)
    
    lon = np.linspace(bottomLeft[1], bottomRight[1], num=num)
    lat = np.linspace(bottomLeft[0], topLeft[0], num=num)

    lat1 = radians(lat[0])
    lon1 = radians(lon[0])
    lat2 = radians(lat[0])
    lon2 = radians(lon[1])

    distance_horizontal = distance(lat1,lon1,lat2,lon2)

    lat1 = radians(lat[0])
    lon1 = radians(lon[0])
    lat2 = radians(lat[1])
    lon2 = radians(lon[0])

    distance_vertical = distance(lat1,lon1,lat2,lon2)

    print(f'{city} has zones of size {round(distance_horizontal,3)} x {round(distance_vertical,3)} km corresponding to {round(distance_horizontal*distance_vertical,3)} km^2')

In [65]:
GridSize("New York", NY_num)

New York has zones of size 0.377 x 0.969 km corresponding to 0.366 km^2


In [66]:
GridSize("London", L_num)

London has zones of size 0.623 x 0.535 km corresponding to 0.333 km^2


In [67]:
# Concat data with grid from New York and London to create one dataframe 
df_L = df_L.dropna(subset=['Grid']).reset_index(drop=True)
df_NY = df_NY.dropna(subset=['Grid']).reset_index(drop=True)
df_L['Grid'] = "L"+df_L['Grid'].astype(int).astype(str)
df_NY['Grid'] = "NY"+df_NY['Grid'].astype(int).astype(str)
places = pd.concat([df_L,df_NY]).reset_index(drop=True)

In [68]:
# Plot places in NY city
df_folium_map_NY=places.loc[places.city == 'New York'][['gPlusPlaceId','lat','lon', 'address']].set_index('gPlusPlaceId')
scatter_map = CreateFastScatterMap(df_folium_map_NY,NY_location)
scatter_map

In [69]:
# Plot the places in London
df_folium_map_L = places.loc[places.city == 'London'][['gPlusPlaceId','lat','lon', 'address']].set_index('gPlusPlaceId')#.head(5000)
scatter_map = CreateFastScatterMap(df_folium_map_L, L_location)
scatter_map

In [70]:
# Save the cleaned places
places.to_csv(data_path + "places_cleaned.csv", index=False)

## Reviews

In [71]:
# The reviews data inlude 571724 ratings including 7 features
reviews.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 571724 entries, 0 to 571723
Data columns (total 8 columns):
 #   Column          Non-Null Count   Dtype  
---  ------          --------------   -----  
 0   rating          571724 non-null  object 
 1   reviewerName    569585 non-null  object 
 2   reviewText      425120 non-null  object 
 3   categories      521628 non-null  object 
 4   gPlusPlaceId    567839 non-null  object 
 5   unixReviewTime  522654 non-null  float64
 6   reviewTime      520907 non-null  object 
 7   gPlusUserId     566092 non-null  object 
dtypes: float64(1), object(7)
memory usage: 34.9+ MB


In [72]:
# Lets consider the missing values
reviews.isna().sum()

rating                 0
reviewerName        2139
reviewText        146604
categories         50096
gPlusPlaceId        3885
unixReviewTime     49070
reviewTime         50817
gPlusUserId         5632
dtype: int64

In [73]:
# Only get reviews that are in the places cleaned dataframe
reviews = reviews.loc[lambda x: x.gPlusPlaceId.isin(places.gPlusPlaceId.values)].reset_index(drop=True)

In [74]:
# Convert rating to numeric feature
reviews['rating'] = pd.to_numeric(reviews['rating'], errors = "coerce")

In [75]:
# Categories are stored as a "['Category']", thus we use regex to find the word between the apostrophes
reviews.dropna(subset=["categories"], inplace=True)
reviews.reset_index(drop=True, inplace=True)

# Categories is essential for our future analysis. Hence we remove rows with missing categories
reviews['categories'] = reviews['categories'].apply(lambda x: re.findall(r"[\[|\s]\'(.*?)\'[\,|\]]", x))

In [76]:
# Each business can have multiple categories but we only want one per business
# We assign the most popular category across the dataset to the respective businesses
def findPopularCat(df):
    popular_dict = df.explode(column = "categories").groupby(["categories"]).count()['gPlusUserId'].to_dict()
    temp_df = df.drop_duplicates(subset="gPlusPlaceId").reset_index(drop=True)
    category_dict = {}
    for _, row in temp_df.iterrows():
        max_count = 0
        max_cat = ""
        for cat in row['categories']:
            count = popular_dict[cat]
            if count > max_count:
                max_count = count
                max_cat = cat
        category_dict[row['gPlusPlaceId']] = max_cat
    return category_dict

category_dict = findPopularCat(reviews)
places['category'] = places['gPlusPlaceId'].apply(lambda x: category_dict[x] if x in category_dict.keys() else np.NaN)
places.dropna(subset=["category"], inplace=True)

In [77]:
# Text processing function
def cleanString(text):
    if not pd.isna(text):
        tokens = word_tokenize(text) #Tokenizing
        punctuation = [word.lower() for word in tokens if word.isalnum()] # remove punctuation and set to lower case
        lemma = [lemmatizer.lemmatize(word) for word in punctuation] # lemmatize words
        stopwords =  nltk.corpus.stopwords.words('english')
        return " ".join([w for w in lemma if w not in stopwords]) # Finally removes stopwords
    else:
        return np.NaN

In [78]:
# Clean the reviews and save them in new column
reviews['reviewTextClean'] = reviews['reviewText'].apply(cleanString)

In [79]:
# Calculate sentiment of each review
def isnan(string):
    return string != string

def sentiment_scores(sentence):
    sid_obj = SentimentIntensityAnalyzer()
    sentiment_dict = sid_obj.polarity_scores(sentence)
    pos = sentiment_dict['pos']
    neg = sentiment_dict['neg']
    neu = sentiment_dict['neu']
    return pos, neg, neu 


reviews['posReviewPercent'] = np.nan
reviews['negReviewPercent'] = np.nan
reviews['midReviewPercent'] = np.nan

i = 0
for r in tqdm(reviews['reviewText']):
    if isnan(r):
        i += 1
        pass
    else:
        pos, neg, neu = sentiment_scores(reviews['reviewText'][i])
        reviews.loc[i, 'posReviewPercent'] = pos
        reviews.loc[i, 'negReviewPercent'] = neg
        reviews.loc[i, 'midReviewPercent'] = neu
        i += 1
 

100%|██████████| 257122/257122 [49:38<00:00, 86.32it/s]  


In [80]:
# Share of reviews without sentiment score
reviews.posReviewPercent.isna().sum()/reviews.shape[0]

0.2693662930437691

In [81]:
# Drop attributes that we are not going to use  
reviews.drop(["categories", "unixReviewTime", "reviewTime"], axis=1, inplace=True)

In [82]:
# Save the cleaned data
reviews.to_csv(data_path + "reviews_cleaned.csv", index=False)
places.to_csv(data_path + "places_cleaned.csv", index=False)